# Clustering examples

This notebook is for developing the fuzzy clustering package and demonstrating how to use it with scikit-learn.

The basic idea is that we create some scikit-learn compatible clustering estimators and a group of scoring functions. They can then be thrown about using scikit-learn for the following important purposes.

* [Pipelines](https://scikit-learn.org/stable/modules/generated/sklearn.pipeline.Pipeline.html) : Chain together pre-processing, clustering and scoring steps into one object
* [Model evaluation](https://scikit-learn.org/stable/model_selection.html#model-selection) : Cross validation of models to find optimum fitting parameters as scored against various scoring functions

We aim to build clustering estimators and store them in ./Models and maybe add:

* Ensemble methods (run many times to assess stability)
* I/O helper functions (read csv, netcdf, whatever)
* Suite of scoring metrics (fuzzy silouette score, partition coefficient, etc)
* Default, pretrained models (one for each common dataset, like OLCI, OC-CCI etc)

in a way that is generalised to work on all models. Must be a scikit-learn compatible object and must not (!) reinvent wheels here

In [1]:
# import the whole package
import fuzzy_water_clustering as fwc

In [2]:
# for serialization of arbitrary Python objects
import pickle
import joblib

# scikit-learn objects for many things
from sklearn.datasets import make_blobs
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.metrics import silhouette_score #, pairwise_distances, make_scorer, 
# from sklearn.metrics.cluster import calinski_harabasz_score, davies_bouldin_score, silhouette_samples, silhouette_score
from sklearn.pipeline import make_pipeline
from sklearn.model_selection import GridSearchCV

# for data handling and visualization
import pandas as pd
import hvplot.pandas
import xarray as xr
import hvplot.xarray
import holoviews as hv
import numpy as np
from functools import reduce

Create a dummy data set

In [3]:
blobs, labels = make_blobs(n_samples=2000, n_features=11)
dfb = pd.DataFrame(blobs.T)

In [4]:
dfb.head(10)

0         1         2         3          4         5         6     \
0  0.368694  2.523551 -5.381843  2.238644  -5.113458 -5.173159  2.904988   
1  9.038225  2.578645 -2.724493  2.562185  -5.399757 -4.653503  2.003777   
2  7.188944  2.192194  1.912159  2.524419   0.488305  1.244604  3.641781   
3  2.045080 -7.119430  2.314432 -6.022023   2.588340  3.230175 -6.550028   
4  6.781691 -1.278736  1.799911 -1.623867  -0.038723  2.935575 -1.481463   
5 -9.908118 -6.192063 -8.702884 -7.058058  -8.240736 -7.201284 -6.307084   
6 -0.336312  9.930075  4.302595  8.446236   5.556722  5.802839  8.091129   
7 -5.193278  8.269257  3.918712  7.096633   4.352942  6.622406  8.476784   
8 -2.101435  3.636196 -9.060221  2.770451 -11.469834 -9.740164  5.109441   
9 -9.467696  2.250581  5.777756  2.431078   4.112466  3.202179  3.970502   

       7          8          9     ...       1990      1991       1992  \
0  2.740996  -5.613825  -2.670772  ...  -1.811244  2.639362  -1.758151   
1  4.540650  -4.199895   5.688406  ...   6.116830  1.128917   7.847119   
2  1.356841   0.995846  10.763409  ...   9.772352  1.503686  12.171680   
3 -6.590329   2.184308  -0.931872  ...   0.444247 -8.862625   0.300374   
4 -0.516868   2.521207  10.014039  ...   7.015294 -0.718462  11.239917   
5 -6.826224  -7.916734  -8.513652  ...  -8.175208 -5.688532  -7.464792   
6  7.995706   5.151378   0.004635  ...  -0.455737  7.914382   1.289442   
7  8.852187   5.760744  -5.144838  ...  -7.640961  8.409035  -5.478447   
8  3.651616 -10.016012  -1.913827  ...  -1.783568  3.697330  -1.464553   
9  2.936430   5.123606  -6.711068  ... -10.251941  2.501158  -7.903445   

        1993      1994      1995      1996       1997      1998      1999  
0   4.001593 -6.393035 -5.919742 -4.166554  -5.891578  3.776220  0.071558  
1   2.509212 -3.273075 -2.948226 -3.909196  -4.091580  1.868768  7.222317  
2   0.223997 -0.874566  1.770549  1.293516   2.618508  1.174236  9.990010  
3  -7.609419  1.681602  3.105023  1.533004   1.856906 -5.724462 -0.039013  
4  -0.696045  3.311447  2.150094  2.481802  -0.047204 -0.899837  9.571363  
5  -5.958199 -8.484044 -8.310286 -7.786705  -6.064990 -5.606552 -7.875049  
6  10.313320  5.554115  5.231261  4.975582   5.689883  8.204148  1.460023  
7   9.072678  5.033224  5.199976  4.585639   3.644181  8.880683 -5.512061  
8   4.392618 -8.660447 -9.223310 -9.533554 -11.652746  4.749653 -2.075837  
9   0.990269  4.474358  5.674491  6.054956   4.185483  2.943772 -8.225704  

[10 rows x 2000 columns]

# 1 using cluster estimator

In [5]:
# create a instance of cmeans model, with number of clusters c
cmeans = fwc.CmeansModel(c=3)

In [6]:
# fit against the dataset, this generates a cluster set
cmeans.fit(blobs)

CmeansModel(c=3)

In [7]:
df_cntr = pd.DataFrame(cmeans.cntr_.T)

In [8]:
dfb.T[labels == 0].T.hvplot(kind='line',datashade=True, cmap='Reds', label='Cluster 1') *\
dfb.T[labels == 1].T.hvplot(kind='line',datashade=True, cmap='Blues', label='Cluster 2') *\
dfb.T[labels == 2].T.hvplot(kind='line',datashade=True, cmap='Greens', label='Cluster 3')

:DynamicMap   []
   :Overlay
      .RGB.Cluster_1 :RGB   [index,value]   (R,G,B,A)
      .RGB.Cluster_2 :RGB   [index,value]   (R,G,B,A)
      .RGB.Cluster_3 :RGB   [index,value]   (R,G,B,A)

In [9]:
reduce(lambda a,b:a*b, [dfb.T[labels == i].mean().T.hvplot(c=c) for (i,c) in zip(range(3),['red','blue','green'])]).opts(title='cluster centres')

:Overlay
   .Curve.A_0.I   :Curve   [index]   (0)
   .Curve.A_0.II  :Curve   [index]   (0)
   .Curve.A_0.III :Curve   [index]   (0)

In [10]:
# plot the classified data
df_cntr.hvplot(title='cluster centres found')

:NdOverlay   [Variable]
   :Curve   [index]   (value)

# 2 Performance metrics

if an algorithm comes with its own scoring metric that will be class specific. However, we can get some metrics that are applicable across all methods. 

Scikit-learn has a [suite of metrics](https://scikit-learn.org/stable/modules/classes.html#module-sklearn.metrics)

Probably the best way is to make a scorer object from a scoring function with `sklearn.metrics.make_scorer` which can be placed at after clustering in a pipeline which is then fed to a GridSearch like object.

In [11]:
ss = fwc.cluster_scoring.silhouette_samples(blobs, cmeans.labels_)
hv.Bars(
    np.hstack([sorted(ss[cmeans.labels_==i]) for i in range(3)]),
).opts(title=f"silhouette_score = {np.round(silhouette_score(blobs, cmeans.labels_), 10)}")

:Bars   [x]   (y)

# 3 Pipelines: chaining transforms and estimators together

https://scikit-learn.org/stable/modules/generated/sklearn.pipeline.Pipeline.html

https://scikit-learn.org/stable/modules/compose.html

In [12]:
# easy to make a pipeline with whatever pieces you want
pl = make_pipeline(
    StandardScaler(),
    PCA(),
    fwc.CmeansModel(c=3)     
)

In [13]:
pl.fit(blobs)

Pipeline(steps=[('standardscaler', StandardScaler()), ('pca', PCA()),
                ('cmeansmodel', CmeansModel(c=3))])

### 3.x inverse_transforms to get final results in original space

Each transform step in a pipeline has an inverse_transform method. Enabling us to reverse the trasform so that final results can be projected into the original space.

In this example, scaling of the data and principal component analysis are applied before clustering. Therefore the clusters are defined in a transformed space. Using inverse_transforms we regain the orginal x,y space the data came in.

In [14]:
df_cntr = pd.DataFrame(
    pl['standardscaler'].inverse_transform(
        pl['pca'].inverse_transform(
            pl['cmeansmodel'].cntr_
        )
    )
)

In [15]:
dfb.hvplot(kind='line', datashade=True, width=1000) * \
df_cntr.T.hvplot(kind='line')

:DynamicMap   []
   :Overlay
      .RGB.I       :RGB   [index,value]   (R,G,B,A)
      .NdOverlay.I :NdOverlay   [Variable]
         :Curve   [index]   (value)

# 4 GridSearchCV: Exhaustive search to find best fitting parameters

https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.GridSearchCV.html

One problem we have is that the clustering algorithms performance depends on the fitting parameters (hyper paramters). These are not learnt, rather they determine the behaviour of the algorithm when finding the learnt parameters. GridSearchCV helps by exhaustively fitting the model to the data for every combination of fitting paramters supplied to it. Furthermore, it fits and scores the model to 5 subsets of the data (by default) so that the variance of the score can be measured.

In [16]:
# define a dict of parameters to go through all combinations of values.
# double underscore joins the step name to its parameter
param_grid = {
    'cmeansmodel__c': [2,4,6,8,10],
    'cmeansmodel__m':[1.5,2.0,2.5],
}

In [17]:
# define the scoring metrics you want to evaluate
scoring = {
    'XB': fwc.cluster_scoring.xie_beni,
    'SIL': fwc.cluster_scoring.hard_silouette,
    'FPC': fwc.cluster_scoring.fuzzy_partition_coef,
    'DB': fwc.cluster_scoring.davies_bouldin,
}

In [18]:
# create a grid search cross validation object
gs = GridSearchCV(
    pl,
    param_grid=param_grid,
    scoring=scoring,
    refit='XB',
    n_jobs=4
)

In [19]:
# fitting syntax is just like before. Except now it tries all combinations of parameters,
# scores and refits witht he best according to the chosen refit metric.
gs.fit(blobs)

GridSearchCV(estimator=Pipeline(steps=[('standardscaler', StandardScaler()),
                                       ('pca', PCA()),
                                       ('cmeansmodel', CmeansModel(c=3))]),
             n_jobs=4,
             param_grid={'cmeansmodel__c': [2, 4, 6, 8, 10],
                         'cmeansmodel__m': [1.5, 2.0, 2.5]},
             refit='XB',
             scoring={'DB': <function davies_bouldin at 0x13a733af0>,
                      'FPC': <function fuzzy_partition_coef at 0x13a7338b0>,
                      'SIL': <function hard_silouette at 0x13a50cee0>,
                      'XB': <function xie_beni at 0x13a50ce50>})

In [20]:
# create a pandas.DataFrame that contains the results of the fitting
dfgs = pd.DataFrame(gs.cv_results_)

## 5.x plotting 

In [21]:
reduce(lambda a,b:a*b,[dfgs.hvplot.errorbars(
        col='param_cmeansmodel__m',
        row=None,
        x='param_cmeansmodel__c',
        y=f'mean_test_{x}',
        yerr1=f'std_test_{x}',
    )*dfgs.hvplot(
        col='param_cmeansmodel__m',
        row=None,
        kind='scatter',
        x='param_cmeansmodel__c',
        y=f'mean_test_{x}',
        label=f'{x}',
        legend=True,
        ylim=[-1.5,1.5],
        ylabel="score",
        xlabel=r"# clusters c",
) for x in scoring.keys()]).opts(title="3 blobs, 2000 points", show_legend=True) \
# + \
# dfb.hvplot(
#     kind='line',
#     x='x',
#     y='y',
#     c=gs.best_estimator_['cmeansmodel'].labels_,
#     cmap='rainbow',
#     width=400,
#     s=0.1
# )

:GridSpace   [param_cmeansmodel__m]
   :Overlay
      .ErrorBars.I   :ErrorBars   [param_cmeansmodel__c]   (mean_test_XB,std_test_XB)
      .Scatter.XB    :Scatter   [param_cmeansmodel__c]   (mean_test_XB)
      .ErrorBars.II  :ErrorBars   [param_cmeansmodel__c]   (mean_test_SIL,std_test_SIL)
      .Scatter.SIL   :Scatter   [param_cmeansmodel__c]   (mean_test_SIL)
      .ErrorBars.III :ErrorBars   [param_cmeansmodel__c]   (mean_test_FPC,std_test_FPC)
      .Scatter.FPC   :Scatter   [param_cmeansmodel__c]   (mean_test_FPC)
      .ErrorBars.IV  :ErrorBars   [param_cmeansmodel__c]   (mean_test_DB,std_test_DB)
      .Scatter.DB    :Scatter   [param_cmeansmodel__c]   (mean_test_DB)

# 5 serializing models

If we like our results and we want to save them. There exist a few choices;

* pickle / joblib : stores arbitrary python objects in instruction orientated file. Insecure on loading, not cross platform nor cross version supported. Only open trusted files and best used short term.
* custom serialization : pipeline parameters can be stored to netcdf using utils/serialize_models. But it also isn't cross platform nor cross version supported at present.

## 5.1 pickle/joblib

In [22]:
# store a model as a pickle file
pickle.dump(
    pl,
    open(
        "practice_fitted_pipeline.p",
        "wb"
    )
)

# 6 Application to OLCI data

In [23]:
#THREDDS pathway for Plymouth Sound
GEO_DAILY1km_THREDDS_string = 'http://rsg.pml.ac.uk/thredds/dodsC/SENTINEL3A_OLCI-G13_300m_02-1d'
ds = xr.open_dataset(GEO_DAILY1km_THREDDS_string)

In [30]:
ds = ds.isel(time=0)

In [ ]:
df = ds.to_dataframe()

In [ ]:
df = df.reset_index().pivot_table(index='pixel',columns='wavelength',values='Rrs')

In [ ]:
pl.fit(df)

In [ ]:
df_cntr = pd.DataFrame(
    pl['standardscaler'].inverse_transform(
        pl['pca'].inverse_transform(
            pl['cmeansmodel'].cntr_
        )
    ),
)

In [ ]:

dfb.hvplot(kind='scatter',x='x',y='y', alpha=0.5, s=1) * \
df_cntr.reset_index().hvplot(kind='scatter',x='x',y='y',c='index', cmap='rainbow', s=30)